In [ ]:
import pandas as pd
import mysql.connector
import os
from datetime import datetime

# MySQL connection parameters
db_config = {
    'host': 'localhost',
    'user': 'root',  # Default XAMPP MySQL user
    'password': '1234',  # Default XAMPP MySQL password is empty
    'database': 'sensor_data'
}

In [ ]:


def import_csv_to_mysql(csv_file_path):
    """Import sensor data from CSV to MySQL"""
    try:
        # Read CSV file
        df = pd.read_csv(csv_file_path)

        # Connect to MySQL
        conn = mysql.connector.connect(**db_config)
        cursor = conn.cursor()

        # Insert data into readings table
        for _, row in df.iterrows():
            query = """
            INSERT INTO readings (
                timestamp, sensor_id, humidity, temperature, conductivity, ph,
                nitrogen, phosphorus, potassium, dht_humidity, dht_temperature
            ) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
            """

            values = (
                row['timestamp'],
                row['sensor'],
                row['humidity'],
                row['temperature'],
                row['conductivity'],
                row['ph'],
                row['nitrogen'],
                row['phosphorus'],
                row['potassium'],
                row['dht_humidity'],
                row['dht_temperature']
            )

            cursor.execute(query, values)

        # Commit changes
        conn.commit()
        print(
            f"Successfully imported {len(df)} records from {os.path.basename(csv_file_path)}")

    except Exception as e:
        print(f"Error importing data: {e}")
    finally:
        if 'conn' in locals() and conn.is_connected():
            cursor.close()
            conn.close()
            print("MySQL connection closed")


if __name__ == "__main__":
    # For Sensor1 data
    sensor1_csv = "sensor1_normalized_data.csv"  # Update with your actual file path
    import_csv_to_mysql(sensor1_csv)

    # For Sensor2 data
    # sensor2_csv = "sensor2_normalized_data.csv"  # Update with your actual file path
    # import_csv_to_mysql(sensor2_csv)

Error importing data: 1054 (42S22): Unknown column 'nan' in 'field list'
MySQL connection closed


In [10]:
def read_all_from_sensor1():
    """Read all data from the sensor1 table in the MySQL database."""
    try:
        # Connect to MySQL
        conn = mysql.connector.connect(**db_config)
        cursor = conn.cursor(dictionary=True)

        # Query to select all data
        query = """
        SELECT * FROM readings WHERE sensor_id = 'sensor2'
"""
        cursor.execute(query)

        # Fetch all rows
        rows = cursor.fetchall()
        for row in rows:
            print(row)

    except Exception as e:
        print(f"Error reading data: {e}")
    finally:
        if 'conn' in locals() and conn.is_connected():
            cursor.close()
            conn.close()
            print("MySQL connection closed")


# Call the function to read data
read_all_from_sensor1()

{'reading_id': 10004, 'timestamp': datetime.datetime(2025, 1, 28, 14, 7, 47), 'sensor_id': 'Sensor2', 'humidity': Decimal('0.00'), 'temperature': Decimal('0.00'), 'conductivity': 0, 'ph': Decimal('0.0'), 'nitrogen': 0, 'phosphorus': 0, 'potassium': 0, 'dht_humidity': Decimal('0.00'), 'dht_temperature': Decimal('0.00'), 'created_at': datetime.datetime(2025, 5, 1, 16, 2, 5)}
{'reading_id': 10005, 'timestamp': datetime.datetime(2025, 1, 28, 14, 7, 52), 'sensor_id': 'Sensor2', 'humidity': Decimal('72.70'), 'temperature': Decimal('26.80'), 'conductivity': 3877, 'ph': Decimal('3.0'), 'nitrogen': 770, 'phosphorus': 1827, 'potassium': 1833, 'dht_humidity': Decimal('0.00'), 'dht_temperature': Decimal('0.00'), 'created_at': datetime.datetime(2025, 5, 1, 16, 2, 5)}
{'reading_id': 10006, 'timestamp': datetime.datetime(2025, 1, 28, 14, 7, 57), 'sensor_id': 'Sensor2', 'humidity': Decimal('73.50'), 'temperature': Decimal('26.80'), 'conductivity': 3877, 'ph': Decimal('3.4'), 'nitrogen': 770, 'phosphor

In [1]:
import numpy as np
import pandas as pd

In [2]:
df1 = pd.read_csv("sensor1_normalized_data.csv")
df2 = pd.read_csv("sensor2_normalized_data.csv")

In [3]:
df1.dtypes

timestamp           object
sensor              object
humidity           float64
temperature        float64
conductivity         int64
ph                 float64
nitrogen             int64
phosphorus           int64
potassium            int64
dht_humidity       float64
dht_temperature    float64
dtype: object

In [4]:
df2.dtypes

timestamp           object
sensor              object
humidity           float64
temperature        float64
conductivity         int64
ph                 float64
nitrogen             int64
phosphorus           int64
potassium            int64
dht_humidity       float64
dht_temperature    float64
dtype: object

In [5]:
df1['timestamp'] = pd.to_datetime(df1['timestamp'], format='%Y-%m-%d %H:%M:%S')
df2['timestamp'] = pd.to_datetime(df2['timestamp'], format='%Y-%m-%d %H:%M:%S')

In [6]:
df1.dtypes

timestamp          datetime64[ns]
sensor                     object
humidity                  float64
temperature               float64
conductivity                int64
ph                        float64
nitrogen                    int64
phosphorus                  int64
potassium                   int64
dht_humidity              float64
dht_temperature           float64
dtype: object

In [7]:
# Drop rows where nitrogen, phosphorus, or potassium have 0 values in df1
df1 = df1[df1['nitrogen'] != 0]
df1 = df1[df1['phosphorus'] != 0]
df1 = df1[df1['potassium'] != 0]

# Drop rows where nitrogen, phosphorus, or potassium have 0 values in df2
df2 = df2[df2['nitrogen'] != 0]
df2 = df2[df2['phosphorus'] != 0]
df2 = df2[df2['potassium'] != 0]

In [8]:
print(df1.describe())

                           timestamp      humidity   temperature  \
count                          10170  10171.000000  10171.000000   
mean   2025-02-05 06:03:21.143657728     33.519575     16.845630   
min              2025-01-28 14:07:52     29.200000     14.500000   
25%    2025-01-31 11:42:34.249999872     30.500000     15.800000   
50%       2025-02-02 11:12:53.500000     31.900000     16.700000   
75%              2025-02-08 21:30:29     36.900000     17.700000   
max              2025-02-24 06:02:24     45.400000     24.600000   
std                              NaN      3.688098      1.309801   

       conductivity            ph      nitrogen    phosphorus     potassium  \
count  10171.000000  10171.000000  10171.000000  10171.000000  10171.000000   
mean     401.405368      7.795310     44.875234    150.317078    143.433684   
min      204.000000      3.000000      4.000000     55.000000     47.000000   
25%      380.000000      7.400000     40.000000    140.000000    133.00

In [9]:
print(df2.describe())

                           timestamp      humidity   temperature  \
count                          10181  10181.000000  10181.000000   
mean   2025-02-05 06:26:27.107160320     64.059257     18.647490   
min              2025-01-28 14:07:52     48.800000     15.400000   
25%              2025-01-31 11:42:39     59.200000     17.600000   
50%              2025-02-02 11:13:07     66.100000     18.100000   
75%              2025-02-08 22:01:44     68.400000     20.000000   
max              2025-02-24 06:02:24     80.200000     27.100000   
std                              NaN      6.397818      1.656918   

       conductivity            ph      nitrogen    phosphorus     potassium  \
count  10181.000000  10181.000000  10181.000000  10181.000000  10181.000000   
mean    3103.330125      6.006561    608.728809   1453.155977   1456.708673   
min     1406.000000      3.000000    255.000000    635.000000    632.000000   
25%     2257.000000      5.900000    432.000000   1045.000000   1046.00

In [13]:
import mysql.connector
import os
from datetime import datetime
from mysql.connector import errorcode

# MySQL connection parameters
db_config = {
    'host': 'sql308.infinityfree.com',
    'user': 'if0_38940647',  # Default XAMPP MySQL user
    'password': 'VCRFRzF8VZzU4',  # Default XAMPP MySQL password is empty
    'database': 'if0_38940647_greenhouse_data',
    'port':     3306,  # Default MySQL port
    'raise_on_warnings': True,
}

In [14]:
def setup_database():
    """Create database and tables for sensor data."""
    try:
        # Connect to MySQL
        conn = mysql.connector.connect(
            host=db_config['host'],
            user=db_config['user'],
            password=db_config['password'],
            port=db_config['port']
        )
        cursor = conn.cursor()

        # Create database
        cursor.execute("CREATE DATABASE IF NOT EXISTS greenhouse_data")
        cursor.execute("USE greenhouse_data")

        # Create table for sensor1 data
        cursor.execute("""
        CREATE TABLE IF NOT EXISTS sensor1 (
            id INT AUTO_INCREMENT PRIMARY KEY,
            timestamp DATETIME NOT NULL,
            sensor_id VARCHAR(50) NOT NULL,
            humidity FLOAT,
            temperature FLOAT,
            conductivity INT,
            ph FLOAT,
            nitrogen INT,
            phosphorus INT,
            potassium INT,
            dht_humidity FLOAT,
            dht_temperature FLOAT,
            created_at TIMESTAMP DEFAULT CURRENT_TIMESTAMP
        )
        """)

        # Create table for sensor2 data
        cursor.execute("""
        CREATE TABLE IF NOT EXISTS sensor2 (
            id INT AUTO_INCREMENT PRIMARY KEY,
            timestamp DATETIME NOT NULL,
            sensor_id VARCHAR(50) NOT NULL,
            humidity FLOAT,
            temperature FLOAT,
            conductivity INT,
            ph FLOAT,
            nitrogen INT,
            phosphorus INT,
            potassium INT,
            dht_humidity FLOAT,
            dht_temperature FLOAT,
            created_at TIMESTAMP DEFAULT CURRENT_TIMESTAMP
        )
        """)

        # Create indexes for faster retrieval
        cursor.execute(
            "CREATE INDEX idx_sensor1_timestamp ON sensor1(timestamp)")
        cursor.execute(
            "CREATE INDEX idx_sensor2_timestamp ON sensor2(timestamp)")

        cursor.execute(
            "CREATE INDEX idx_sensor1_sensor_id ON sensor1(sensor_id)")
        cursor.execute(
            "CREATE INDEX idx_sensor2_sensor_id ON sensor2(sensor_id)")

        # Insert data from df1 into sensor1 table
        for _, row in df1.iterrows():
            cursor.execute("""
            INSERT INTO sensor1 (
            timestamp, sensor_id, humidity, temperature, conductivity, ph, nitrogen,
            phosphorus, potassium, dht_humidity, dht_temperature
            ) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
            """, (
                row['timestamp'], row['sensor'], row['humidity'], row['temperature'], row['conductivity'],
                row['ph'], row['nitrogen'], row['phosphorus'], row['potassium'],
                row['dht_humidity'], row['dht_temperature']
            ))

        # Insert data from df2 into sensor2 table
        for _, row in df2.iterrows():
            cursor.execute("""
            INSERT INTO sensor2 (
            timestamp, sensor_id, humidity, temperature, conductivity, ph, nitrogen,
            phosphorus, potassium, dht_humidity, dht_temperature
            ) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
            """, (
                row['timestamp'], row['sensor'], row['humidity'], row['temperature'], row['conductivity'],
                row['ph'], row['nitrogen'], row['phosphorus'], row['potassium'],
                row['dht_humidity'], row['dht_temperature']
            ))

        # Commit changes
        conn.commit()
        print("Database and tables created successfully.")

    except mysql.connector.Error as err:
        if err.errno == errorcode.ER_ACCESS_DENIED_ERROR:
            print("Authentication error: check your username/password")
        elif err.errno == errorcode.ER_BAD_DB_ERROR:
            print(f"Database does not exist: {db_config['database']}")
        else:
            print(f"Unexpected error: {err}")
    finally:
        if conn.is_connected():
            cursor.close()
            conn.close()
            print("MySQL connection closed.")


# Call the function to set up the database
setup_database()

Unexpected error: 2005 (HY000): Unknown MySQL server host 'sql308.infinityfree.com' (11001)


UnboundLocalError: cannot access local variable 'conn' where it is not associated with a value

In [23]:
def retrieve_data_from_tables():
    """Retrieve data from both sensor1 and sensor2 tables."""
    try:
        # Connect to MySQL
        conn = mysql.connector.connect(**db_config)
        cursor = conn.cursor(dictionary=True)

        cursor.execute("USE greenhouse_data")
        # Query to retrieve data from sensor1
        query_sensor1 = "SELECT * FROM sensor1"
        cursor.execute(query_sensor1)
        sensor1_data = cursor.fetchall()
        print("Data from sensor1:")
        for row in sensor1_data:
            print(row)

        # # Query to retrieve data from sensor2
        # query_sensor2 = "SELECT * FROM sensor2"
        # cursor.execute(query_sensor2)
        # sensor2_data = cursor.fetchall()
        # print("\nData from sensor2:")
        # for row in sensor2_data:
        #     print(row)

    except Exception as e:
        print(f"Error retrieving data: {e}")
    finally:
        if 'conn' in locals() and conn.is_connected():
            cursor.close()
            conn.close()
            print("MySQL connection closed")


# Call the function to retrieve data
retrieve_data_from_tables()

Data from sensor1:
{'id': 1, 'timestamp': datetime.datetime(2025, 1, 28, 14, 7, 52), 'sensor_id': 'Sensor1', 'humidity': 32.2, 'temperature': 24.4, 'conductivity': 461, 'ph': 3.0, 'nitrogen': 57, 'phosphorus': 179, 'potassium': 172, 'dht_humidity': 0.0, 'dht_temperature': 0.0, 'created_at': datetime.datetime(2025, 5, 1, 22, 21, 47)}
{'id': 2, 'timestamp': datetime.datetime(2025, 1, 28, 14, 7, 57), 'sensor_id': 'Sensor1', 'humidity': 32.0, 'temperature': 24.5, 'conductivity': 461, 'ph': 4.6, 'nitrogen': 57, 'phosphorus': 179, 'potassium': 172, 'dht_humidity': 0.0, 'dht_temperature': 0.0, 'created_at': datetime.datetime(2025, 5, 1, 22, 21, 47)}
{'id': 3, 'timestamp': datetime.datetime(2025, 1, 28, 14, 8, 2), 'sensor_id': 'Sensor1', 'humidity': 33.0, 'temperature': 24.5, 'conductivity': 461, 'ph': 8.2, 'nitrogen': 57, 'phosphorus': 179, 'potassium': 172, 'dht_humidity': 0.0, 'dht_temperature': 0.0, 'created_at': datetime.datetime(2025, 5, 1, 22, 21, 47)}
{'id': 4, 'timestamp': datetime.da